## Intraday vwap mean reverting

Desription: mean reverting intraday strategy with momentum entry

Goal is to recreate strategy in vectorbptro and compare with v2trading engine backtest.

Symbol: BAC
Timeframe: 12s
Backtested on: 1s
Entry window: 0 - 380 (mins. from open)
EOD Exit: 382-390

Indicators:
- vwap_cum - Anchored daily cumulative vwap 
- div_vwap_cum - Divergence of vwap_cum and close 
- div_vwap_angle - Linreg angle of div_vwap_cum over period N (hp1)

**Long entries:**
- div_vwap_angle.AND.go_short_if_fallingc = 3 (hp2)
- div_vwap_cum.AND.go_short_if_above = 0 (hp3)

**Short entries:**
- div_vwap_angle.AND.go_long_if_risingc = 3 (hp2)
- div_vwap_cum.AND.go_long_if_below = 0 (hp3)

**Exits:**
only SL, TP pct based
- SL: 0.3 (hp4)
- TP: 0.4 (hp5)

hp - hyperparameters for tuning

In [2]:
import vectorbtpro as vbt
import ttools as tts
from lightweight_charts import chart, Panel, PlotDFAccessor, PlotSRAccessor
import talib
from numba import jit
import pandas as pd
import numpy as np


In [3]:
 #fetching from remote db
from lib.db import Connection
SYMBOL = "BAC"
SCHEMA = "ohlcv_1s" #time based 1s other options ohlcv_vol_200 (volume based ohlcv with resolution of 200), ohlcv_renko_20 (renko with 20 bricks size) ...
DB = "market_data"

con = Connection(db_name=DB, default_schema=SCHEMA, create_db=True)
basic_data = con.pull(symbols=[SYMBOL], schema=SCHEMA,start="2024-10-14", end="2024-10-17", tz_convert='America/New_York')

#basic_data = basic_data.add_symbol("BAC2", basic_data.data["BAC"])

#basic_data.index.normalize().nunique()

100%|##########| 1/1 [00:02<00:00,  2.76s/it, symbol=BAC]

In [4]:
basic_data = basic_data[['open',
 'high',
 'low',
 'close',
 'volume']]

In [5]:
#Resample to 12s
s12_data = basic_data.resample("12s")
s12_data = s12_data.transform(lambda df: df.between_time('09:30', '16:00').dropna())

s12_data.data["BAC"].lw.plot()

In [6]:
#s12_data = s12_data.add_symbol("BAC3", s12_data.data["BAC"])
s12_data.symbols

['BAC']

In [7]:
#s12_data = s12_data.add_symbol("BAC-SHORT", s12_data.data["BAC-LONG"])

In [8]:
vbt.IF.list_indicators("*DIV*")

['talib:DIV']

In [9]:
vbt.phelp(vbt.indicator("talib:LINEARREG_ANGLE").run)

LINEARREG_ANGLE.run(
    close,
    timeperiod=Default(value=14),
    timeframe=Default(value=None),
    short_name='linearreg_angle',
    hide_params=None,
    hide_default=True,
    **kwargs
):
    Run `LINEARREG_ANGLE` indicator.
    
    * Inputs: `close`
    * Parameters: `timeperiod`, `timeframe`
    * Outputs: `real`
    
    Pass a list of parameter names as `hide_params` to hide their column levels, or True to hide all.
    Set `hide_default` to False to show the column levels of the parameters with a default value.
    
    Other keyword arguments are passed to `LINEARREG_ANGLE.run_pipeline`.


In [10]:
from numba import jit
import numpy as np

@jit(nopython=True)
def isrisingc(pole: np.ndarray, pocet: int) -> np.ndarray:
    # Ensure pocet is valid
    if pocet < 1 or pocet > pole.shape[0]:
        raise ValueError("Invalid window size.")

    # Create a result array initialized to False
    result = np.zeros(pole.shape[0], dtype=np.bool_)

    # Iterate through the array, starting from the first valid rolling window
    for i in range(pocet - 1, pole.shape[0]):
        is_increasing = True
        # Compare the current value with the previous value within the rolling window
        for j in range(i - pocet + 2, i + 1):  # Start comparison from the second element in the window
            if pole[j] <= pole[j - 1]:  # Check if current element is not greater than the previous one
                is_increasing = False
                break
        result[i] = is_increasing

    return result


In [11]:
#s12_data.ohlcv.data["BAC"].vbt.xloc[slice("2024-10-14 15:50:00", "2024-10-15 15:50:00")].obj.head(10)

# a = div_vwap_cum.xloc[slice("2024-10-14 15:50:00", "2024-10-15 15:50:00")].div.head(60)
# a

In [12]:
s12_data.close

symbol                         BAC
time                              
2024-10-14 09:30:00-04:00  42.0737
2024-10-14 09:30:12-04:00  42.0750
2024-10-14 09:30:24-04:00  42.0650
2024-10-14 09:30:36-04:00  42.0300
2024-10-14 09:30:48-04:00  41.9700
...                            ...
2024-10-16 15:59:00-04:00  42.7550
2024-10-16 15:59:12-04:00  42.7700
2024-10-16 15:59:24-04:00  42.7800
2024-10-16 15:59:36-04:00  42.7900
2024-10-16 15:59:48-04:00  42.8100

[5842 rows x 1 columns]

In [13]:
basic_data.data["BAC"].head(50)

open     high      low    close    volume
time                                                                   
2024-10-14 09:30:01-04:00  41.9600  42.0450  41.8200  41.9650  429666.0
2024-10-14 09:30:02-04:00  41.9536  41.9900  41.9536  41.9800     895.0
2024-10-14 09:30:03-04:00  41.9900  42.0100  41.9900  42.0050   15707.0
2024-10-14 09:30:04-04:00  42.0100  42.0800  42.0100  42.0600   22696.0
2024-10-14 09:30:05-04:00  42.0400  42.0500  42.0200  42.0400     525.0
2024-10-14 09:30:06-04:00  42.0000  42.0300  41.9900  42.0100    8735.0
2024-10-14 09:30:07-04:00  42.0200  42.0400  42.0200  42.0200     400.0
2024-10-14 09:30:08-04:00  42.0600  42.0600  42.0600  42.0600     100.0
2024-10-14 09:30:09-04:00  42.0200  42.0200  42.0200  42.0200     100.0
2024-10-14 09:30:10-04:00  42.0473  42.0600  42.0400  42.0600    1614.0
2024-10-14 09:30:11-04:00  42.0600  42.0737  42.0600  42.0737    2100.0
2024-10-14 09:30:13-04:00  42.0848  42.0900  42.0848  42.0900    5179.0
2024-10-14 09:30:14-04:00  42.0700  42.0800  42.0700  42.0800     200.0
2024-10-14 09:30:15-04:00  42.0700  42.0900  42.0700  42.0850    5875.0
2024-10-14 09:30:16-04:00  42.0800  42.0900  42.0800  42.0850     951.0
2024-10-14 09:30:17-04:00  42.0850  42.0900  42.0750  42.0900    1100.0
2024-10-14 09:30:18-04:00  42.0800  42.0900  42.0550  42.0900    4242.0
2024-10-14 09:30:19-04:00  42.0900  42.0900  42.0600  42.0650    3214.0
2024-10-14 09:30:20-04:00  42.0721  42.0721  42.0650  42.0650    6666.0
2024-10-14 09:30:21-04:00  42.0650  42.0650  42.0650  42.0650     500.0
2024-10-14 09:30:22-04:00  42.0700  42.0700  42.0650  42.0650   10100.0
2024-10-14 09:30:23-04:00  42.0700  42.0750  42.0650  42.0750     800.0
2024-10-14 09:30:24-04:00  42.0700  42.0900  42.0700  42.0900     800.0
2024-10-14 09:30:25-04:00  42.0900  42.0900  42.0600  42.0600    2622.0
2024-10-14 09:30:26-04:00  42.0550  42.0750  42.0500  42.0500    2530.0
2024-10-14 09:30:27-04:00  42.0650  42.0650  42.0550  42.0600    1222.0
2024-10-14 09:30:28-04:00  42.0300  42.0300  42.0300  42.0300    1200.0
2024-10-14 09:30:29-04:00  42.0400  42.0600  42.0400  42.0600    2345.0
2024-10-14 09:30:30-04:00  42.0600  42.0600  42.0500  42.0500    2417.0
2024-10-14 09:30:31-04:00  42.0500  42.0500  42.0500  42.0500     100.0
2024-10-14 09:30:32-04:00  42.0500  42.0600  42.0500  42.0600     775.0
2024-10-14 09:30:33-04:00  42.0500  42.0500  42.0500  42.0500     100.0
2024-10-14 09:30:35-04:00  42.0600  42.0650  42.0489  42.0650     750.0
2024-10-14 09:30:36-04:00  42.0650  42.0850  42.0650  42.0700    1614.0
2024-10-14 09:30:37-04:00  42.0800  42.0800  42.0700  42.0700     300.0
2024-10-14 09:30:38-04:00  42.0600  42.0600  42.0600  42.0600     100.0
2024-10-14 09:30:39-04:00  42.0550  42.0600  42.0550  42.0600     963.0
2024-10-14 09:30:41-04:00  42.0500  42.0500  42.0201  42.0201    1301.0
2024-10-14 09:30:42-04:00  42.0400  42.0400  42.0350  42.0350    1300.0
2024-10-14 09:30:43-04:00  42.0200  42.0350  42.0200  42.0300    3123.0
2024-10-14 09:30:44-04:00  42.0362  42.0362  42.0300  42.0350     500.0
2024-10-14 09:30:45-04:00  42.0331  42.0331  42.0200  42.0200     900.0
2024-10-14 09:30:46-04:00  42.0400  42.0400  42.0400  42.0400     112.0
2024-10-14 09:30:47-04:00  42.0200  42.0300  42.0200  42.0300     300.0
2024-10-14 09:30:48-04:00  42.0200  42.0200  42.0050  42.0050    1166.0
2024-10-14 09:30:50-04:00  42.0200  42.0200  42.0200  42.0200    1207.0
2024-10-14 09:30:51-04:00  42.0100  42.0100  42.0100  42.0100     209.0
2024-10-14 09:30:53-04:00  42.0100  42.0150  42.0100  42.0100    2490.0
2024-10-14 09:30:54-04:00  42.0100  42.0100  42.0100  42.0100     600.0
2024-10-14 09:30:56-04:00  42.0100  42.0100  42.0100  42.0100     400.0

In [14]:
# long_entries = tts.isrisingc(dvla,3).vbt & div_vwap_cum.div_below(0)
# long_entries = long_entries.vbt.realign_closing(basic_data.index, ffill=False, freq="1s").dropna().astype(bool)


In [15]:
%load_ext autoreload
%autoreload 2
from ttools.vbtindicators import register_custom_inds
register_custom_inds(None, "override")
#chopiness = vbt.indicator("technical:CHOPINESS").run(s12_data.open, s12_data.high, s12_data.low, s12_data.close, s12_data.volume, window = 100)
#vwap_cum_roll = vbt.indicator("technical:ROLLING_VWAP").run(s12_data.open, s12_data.high, s12_data.low, s12_data.close, s12_data.volume, window = 100, min_periods = 5)

#note that VWAP is calculated from HLCC4 rounded to 3 decimals, can be changed by hlcc4_round parameter
vwap_cum_d = vbt.indicator("ttools:CUVWAP").run(s12_data.high, s12_data.low, s12_data.close, s12_data.volume, anchor=vbt.Default(value="D"), drag=vbt.Default(value=50), hide_default=True)
div_vwap_cum = vbt.indicator("ttools:DIVERGENCE").run(s12_data.close, vwap_cum_d.vwap, divtype=vbt.Default(value="reln"), hide_default=True)
div_vwap_lin_angle = vbt.indicator("talib:LINEARREG_ANGLE").run(div_vwap_cum.div, timeperiod=2)
dvla = np.round(div_vwap_lin_angle.real,4)

long_entries = tts.isrisingc(dvla,3).vbt & div_vwap_cum.div_below(0)
short_entries = tts.isfallingc(dvla,3).vbt & div_vwap_cum.div_above(0)

#SIGNAL - make indicator with 1 - long, -1 - short, 0 nothing
long_series = long_entries.squeeze()
short_series = short_entries.squeeze()
signals = pd.Series(0, index=long_series.index)  # Initialize with 0
signals[long_series] = 1  # Set 1 where entries are True
signals[short_series] = -1   # Set -1 where exits are True

Panel(
    ohlcv=(s12_data.ohlcv.data["BAC"],), #[(long_entries.squeeze())],[(short_entries.squeeze())]),
    right=[(vwap_cum_d.vwap, "vwap_cum_daily")], 
    middle1=[(dvla, "div_vwap_angle")],
    middle2=[(signals, "signals")],
    left=[(div_vwap_cum.div, "div_vwap_cum")]).chart(size="m", xloc=slice("2024-10-14 15:00:00", "2024-10-15 16:00:00"), precision=4)

In [16]:
#TED backtest, porovnat s v2realbot, delsi obdobi, tuning parametru a zpetne vyzkouseni s realbotem
#pripadne mrknout na markov variance switching zda nepujde na intraday

In [31]:
from typing import Any
from ttools import create_mask_from_window

#single for exits, as it is just EOD exits
exits = pd.DataFrame.vbt.signals.empty_like(long_entries) 
entry_window_opens = 0 #in minutes from start of the market
entry_window_closes = 380
forced_exit_start = 382
forced_exit_end = 390

#create mask based on main session that day
entry_window_opened = create_mask_from_window(long_entries, entry_window_opens, entry_window_closes, use_cal=False)
#limit entries to the window
long_entries_cln = long_entries.vbt & entry_window_opened
short_entries_cln = short_entries.vbt & entry_window_opened

#create forced exits mask
forced_exits_window = create_mask_from_window(exits, forced_exit_start, forced_exit_end, use_cal=False)

#add just forced EOD exits to exits, series is ok
long_exits = forced_exits_window
short_exits = forced_exits_window

In [64]:
from collections import namedtuple
from numba import njit
from numba import config

#callback function in separate file signal_func_nb.py, this one is just for debugging
#@njit
def signal_func_nb(c, entries, exits, short_entries, short_exits, cooldown_time, cooldown_bars):
    entry = vbt.pf_nb.select_nb(c, entries)
    exit = vbt.pf_nb.select_nb(c, exits)
    short_entry = vbt.pf_nb.select_nb(c, short_entries)
    short_exit = vbt.pf_nb.select_nb(c, short_exits)
    if not vbt.pf_nb.in_position_nb(c): #c.last_position == 0
        if vbt.pf_nb.has_orders_nb(c):  
            last_exit_idx = c.last_pos_info[c.col]["exit_idx"] #(92)  #If not in position, position information records contain information on the last (closed) position
            if cooldown_time is not None and c.index[c.i] - c.index[last_exit_idx] < cooldown_time:
                return False, exit, False, short_exit #disable entry
            elif cooldown_bars is not None and last_exit_idx + cooldown_bars > c.i:
                return False, exit, False, short_exit #disable entry
    return entry, exit, short_entry, short_exit

cooldown_time = None #vbt.dt.to_ns(vbt.timedelta("2m"))
cooldown_bars = 5
size=100

pf = vbt.Portfolio.from_signals(
    close=s12_data.close,
    entries=long_entries_cln,
    exits=long_exits,
    short_entries=short_entries_cln,
    short_exits=short_exits,
    signal_func_nb="signal_func_nb.py",
    #signal_func_nb=signal_func_nb,
    signal_args=(
        vbt.Rep("entries"), 
        vbt.Rep("exits"),
        vbt.Rep("short_entries"),
        vbt.Rep("short_exits"),
        cooldown_time, # cooldown in timedelta in ns after exit
        cooldown_bars  #cooldown in number of bars after exit
    ),
    sl_stop=0.3,
    tp_stop = 0.4,
    delta_format = vbt.pf_enums.DeltaFormat.Percent100, #(Absolute, Percent, Percent100, Target)
    fees=0.0167/100,
    freq="12s",
    size=size, # pf_enums.SizeType.Amount (Absolute, Percent, Percent100, Target)
    staticized=True,
    #jitted=False
    ) #sl_stop=sl_stop, tp_stop = sl_stop,, tsl_stop


In [66]:
#TODO - charting trades in lw from pf.trades
#obecne analyza trades a vizualizace
#grafy vykonu, cas atp. + potom hyperparamater testing

pf.xloc["2024-10-15"].stats()





Start Index                   2024-10-15 09:30:00-04:00
End Index                     2024-10-15 15:59:48-04:00
Total Duration                          0 days 06:29:36
Start Value                                  101.713787
Min Value                                    101.696804
Max Value                                     104.96345
End Value                                    103.671538
Total Return [%]                               1.924764
Benchmark Return [%]                          -2.498843
Position Coverage [%]                         90.811088
Max Gross Exposure [%]                        100.58714
Max Drawdown [%]                               1.230821
Max Drawdown Duration                   0 days 04:47:24
Total Orders                                         37
Total Fees Paid                                 0.72742
Total Trades                                         21
Win Rate [%]                                  66.666667
Best Trade [%]                                 0

In [65]:
pf.xloc[slice("2024-10-15 09:30:00", "2024-10-15 16:00:00")].trades.plot()

FigureWidget({
    'data': [{'line': {'color': '#1f77b4'},
              'mode': 'lines',
              'name': 'Close',
              'showlegend': True,
              'type': 'scatter',
              'uid': '0e026941-121f-4b79-86a4-de7599b923b9',
              'x': array([datetime.datetime(2024, 10, 15, 9, 30, tzinfo=<DstTzInfo 'America/New_York' EDT-1 day, 20:00:00 DST>),
                          datetime.datetime(2024, 10, 15, 9, 30, 12, tzinfo=<DstTzInfo 'America/New_York' EDT-1 day, 20:00:00 DST>),
                          datetime.datetime(2024, 10, 15, 9, 30, 24, tzinfo=<DstTzInfo 'America/New_York' EDT-1 day, 20:00:00 DST>),
                          ...,
                          datetime.datetime(2024, 10, 15, 15, 59, 24, tzinfo=<DstTzInfo 'America/New_York' EDT-1 day, 20:00:00 DST>),
                          datetime.datetime(2024, 10, 15, 15, 59, 36, tzinfo=<DstTzInfo 'America/New_York' EDT-1 day, 20:00:00 DST>),
                          datetime.datetime(2024, 10, 15,

In [50]:
pf.xloc[slice("2024-10-15 09:30:00", "2024-10-15 16:00:00")].orders.readable

Order Id    Column              Signal Index            Creation Index  \
0         30  (2, BAC) 2024-10-15 09:30:48-04:00 2024-10-15 09:30:48-04:00   
1         31  (2, BAC) 2024-10-15 09:30:48-04:00 2024-10-15 09:31:48-04:00   
2         32  (2, BAC) 2024-10-15 09:33:24-04:00 2024-10-15 09:33:24-04:00   
3         33  (2, BAC) 2024-10-15 09:33:24-04:00 2024-10-15 09:35:00-04:00   
4         34  (2, BAC) 2024-10-15 09:37:00-04:00 2024-10-15 09:37:00-04:00   
5         35  (2, BAC) 2024-10-15 09:37:00-04:00 2024-10-15 09:45:12-04:00   
6         36  (2, BAC) 2024-10-15 09:46:36-04:00 2024-10-15 09:46:36-04:00   
7         37  (2, BAC) 2024-10-15 09:46:36-04:00 2024-10-15 09:48:00-04:00   
8         38  (2, BAC) 2024-10-15 09:50:00-04:00 2024-10-15 09:50:00-04:00   
9         39  (2, BAC) 2024-10-15 09:50:00-04:00 2024-10-15 09:54:24-04:00   
10        40  (2, BAC) 2024-10-15 09:57:00-04:00 2024-10-15 09:57:00-04:00   
11        41  (2, BAC) 2024-10-15 09:57:00-04:00 2024-10-15 10:06:36-04:00   
12        42  (2, BAC) 2024-10-15 10:07:48-04:00 2024-10-15 10:07:48-04:00   
13        43  (2, BAC) 2024-10-15 10:07:48-04:00 2024-10-15 10:12:12-04:00   
14        44  (2, BAC) 2024-10-15 10:13:12-04:00 2024-10-15 10:13:12-04:00   
15        45  (2, BAC) 2024-10-15 10:14:24-04:00 2024-10-15 10:14:24-04:00   
16        46  (2, BAC) 2024-10-15 10:20:36-04:00 2024-10-15 10:20:36-04:00   
17        47  (2, BAC) 2024-10-15 11:08:12-04:00 2024-10-15 11:08:12-04:00   
18        48  (2, BAC) 2024-10-15 11:08:12-04:00 2024-10-15 11:17:00-04:00   
19        49  (2, BAC) 2024-10-15 11:20:00-04:00 2024-10-15 11:20:00-04:00   
20        50  (2, BAC) 2024-10-15 11:20:00-04:00 2024-10-15 12:22:24-04:00   
21        51  (2, BAC) 2024-10-15 12:25:36-04:00 2024-10-15 12:25:36-04:00   
22        52  (2, BAC) 2024-10-15 12:25:36-04:00 2024-10-15 12:44:48-04:00   
23        53  (2, BAC) 2024-10-15 12:53:48-04:00 2024-10-15 12:53:48-04:00   
24        54  (2, BAC) 2024-10-15 13:05:36-04:00 2024-10-15 13:05:36-04:00   
25        55  (2, BAC) 2024-10-15 13:05:36-04:00 2024-10-15 13:22:36-04:00   
26        56  (2, BAC) 2024-10-15 13:24:24-04:00 2024-10-15 13:24:24-04:00   
27        57  (2, BAC) 2024-10-15 13:24:24-04:00 2024-10-15 13:54:24-04:00   
28        58  (2, BAC) 2024-10-15 13:55:24-04:00 2024-10-15 13:55:24-04:00   
29        59  (2, BAC) 2024-10-15 13:55:24-04:00 2024-10-15 14:43:36-04:00   
30        60  (2, BAC) 2024-10-15 14:59:36-04:00 2024-10-15 14:59:36-04:00   
31        61  (2, BAC) 2024-10-15 14:59:36-04:00 2024-10-15 15:36:00-04:00   
32        62  (2, BAC) 2024-10-15 15:37:00-04:00 2024-10-15 15:37:00-04:00   
33        63  (2, BAC) 2024-10-15 15:37:00-04:00 2024-10-15 15:50:12-04:00   

    ...      Fees  Side    Type  Stop Type  
0   ...  0.016968  Sell  Market       None  
1   ...  0.016900   Buy  Market         TP  
2   ...  0.017030  Sell  Market       None  
3   ...  0.016962   Buy  Market         TP  
4   ...  0.017093  Sell  Market       None  
5   ...  0.017025   Buy  Market         TP  
6   ...  0.017156   Buy  Market       None  
7   ...  0.017224  Sell  Market         TP  
8   ...  0.017218  Sell  Market       None  
9   ...  0.017270   Buy  Market         SL  
10  ...  0.017161  Sell  Market       None  
11  ...  0.017092   Buy  Market         TP  
12  ...  0.017224   Buy  Market       None  
13  ...  0.017293  Sell  Market         TP  
14  ...  0.017287   Buy  Market       None  
15  ...  0.034601  Sell  Market       None  
16  ...  0.034589   Buy  Market       None  
17  ...  0.034806  Sell  Market       None  
18  ...  0.017452   Buy  Market         SL  
19  ...  0.017342  Sell  Market       None  
20  ...  0.017394   Buy  Market         SL  
21  ...  0.017284  Sell  Market       None  
22  ...  0.017215   Buy  Market         TP  
23  ...  0.017348  Sell  Market       None  
24  ...  0.034689   Buy  Market       None  
25  ...  0.017329  Sell  Market         SL  
26  ...  0.017323   Buy  Market       None  
27  ...  0.01

In [153]:
a = short_entries_cln.vbt.xloc[slice("2024-10-15 09:35:00", "2024-10-15 16:00:00")].obj
a

linearreg_angle_timeperiod      2
symbol                        BAC
time                             
2024-10-15 09:35:00-04:00    True
2024-10-15 09:35:12-04:00   False
2024-10-15 09:35:24-04:00   False
2024-10-15 09:35:36-04:00   False
2024-10-15 09:35:48-04:00   False
...                           ...
2024-10-15 15:59:00-04:00   False
2024-10-15 15:59:12-04:00   False
2024-10-15 15:59:24-04:00   False
2024-10-15 15:59:36-04:00   False
2024-10-15 15:59:48-04:00   False

[1923 rows x 1 columns]

In [24]:
pf.xloc["2024-10-15"].stats()

Start Index                   2024-10-15 09:30:00-04:00
End Index                     2024-10-15 15:59:48-04:00
Total Duration                          0 days 06:29:36
Start Value                                  101.047553
Min Value                                    101.047553
Max Value                                    101.047553
End Value                                    101.047553
Total Return [%]                                    0.0
Benchmark Return [%]                          -2.498843
Position Coverage [%]                               0.0
Max Gross Exposure [%]                              0.0
Max Drawdown [%]                                    NaN
Max Drawdown Duration                               NaT
Total Orders                                          0
Total Fees Paid                                     0.0
Total Trades                                          0
Win Rate [%]                                        NaN
Best Trade [%]                                  

In [172]:
pf.xloc[slice("2024-10-15 09:30:00", "2024-10-15 16:00:00")].trades.records_readable



Exit Trade Id    Column      Size  Entry Order Id  \
0               0  (2, BAC)  2.364210              32   
1               1  (2, BAC)  2.386721              34   
2               2  (2, BAC)  2.413778              36   
3               3  (2, BAC)  2.415524              38   
4               4  (2, BAC)  2.434368              40   
5               5  (2, BAC)  2.432979              42   
6               6  (2, BAC)  2.417777              44   
7               7  (2, BAC)  2.443496              46   
8               8  (2, BAC)  2.443536              48   
9               9  (2, BAC)  2.449605              49   
10             10  (2, BAC)  2.448787              50   
11             11  (2, BAC)  2.465854              51   
12             12  (2, BAC)  2.465031              52   
13             13  (2, BAC)  2.452200              54   
14             14  (2, BAC)  2.434196              56   
15             15  (2, BAC)  2.451836              58   
16             16  (2, BAC)  2.459657              59   
17             17  (2, BAC)  2.459539              61   
18             18  (2, BAC)  2.455968              63   
19             19  (2, BAC)  2.455123              65   
20             20  (2, BAC)  2.455883              67   
21             21  (2, BAC)  2.455805              69   

                 Entry Index  Avg Entry Price  Entry Fees  Exit Order Id  \
0  2024-10-15 09:30:48-04:00          43.1000    0.017017             33   
1  2024-10-15 09:32:36-04:00          42.8500    0.017079             35   
2  2024-10-15 09:35:24-04:00          42.5250    0.017142             37   
3  2024-10-15 09:37:00-04:00          42.6500    0.017205             39   
4  2024-10-15 09:46:36-04:00          42.4750    0.017268             41   
5  2024-10-15 09:48:24-04:00          42.6550    0.017331             43   
6  2024-10-15 09:52:00-04:00          42.7801    0.017273             45   
7  2024-10-15 10:07:48-04:00          42.4850    0.017337             47   
8  2024-10-15 10:12:24-04:00          42.6400    0.017400             49   
9  2024-10-15 10:13:12-04:00          42.5800    0.017419             50   
10 2024-10-15 10:14:24-04:00          42.6201    0.017429             51   
11 2024-10-15 10:20:36-04:00          42.4650    0.017487             52   
12 2024-10-15 11:08:12-04:00          42.5900    0.017533             53   
13 2024-10-15 11:20:00-04:00          42.6701    0.017474             55   
14 2024-10-15 12:23:00-04:00          42.8424    0.017416             57   
15 2024-10-15 12:57:36-04:00          42.6901    0.017480             59   
16 2024-10-15 13:05:36-04:00          42.6150    0.017505             60   
17 2024-10-15 13:23:00-04:00          42.4750    0.017446             62   
18 2024-10-15 14:03:00-04:00          42.3950    0.017388             64   
19 2024-10-15 14:44:24-04:00          42.5650    0.017452             66   
20 2024-10-15 15:36:24-04:00          42.4100    0.017394             68   
21 2024-10-15 15:47:12-04:00          42.2700    0.017336             70   

                  Exit Index  Avg Exit Price  Exit Fees       PnL    Return  \
0  2024-10-15 09:31:48-04:00       42.927600   0.016949  0.373624  0.003667   
1  2024-10-15 09:35:00-04:00       42.678600   0.017011  0.374994  0.003667   
2  2024-10-15 09:36:48-04:00       42.695100   0.017210  0.376231  0.003665   
3  2024-10-15 09:45:12-04:00       42.479400   0.017136  0.377748  0.003667   
4  2024-10-15 09:48:00-04:00       42.644900   0.017337  0.378995  0.003665   
5  2024-10-15 09:50:48-04:00       42.782965   0.017383 -0.346050 -0.003335   
6  2024-10-15 10:07:00-04:00       42.608980   0.017204  0.379253  0.003667   
7  2024-10-15 10:12:12-04:00       42.654940   0.017406  0.380505  0.003665   
8  2024-10-15 10:13:12-04:00       42.580000   0.017376  0.111836  0.001073   
9  2024-10-15 10:14:24-04:00       42.620100   0.017435  0.063375  0.000608   
10 2024-10-15 10:20:36-04:00       42.465000   0.017366  0.345011  0.00330

In [154]:
s12_data.wrapper.shape[0]

19393

In [155]:
group_lens =s12_data.wrapper.get_index_grouper("D").get_group_lens()

In [157]:
group_end_idxs = np.cumsum(group_lens)
# # group_start_idxs = group_end_idxs - group_lens

array([    0,  1941,  3871,  5799,  7727,  9669, 11601, 13551, 15500,
       17448])

In [144]:
s12_data.ohlcv.data["BAC-LONG"].lw.plot(right=[(vwap_cum, "vwap")])

In [61]:
import talib
pd.set_option('display.max_rows', 500)
def apply_func_1d(close, high, timeperiod):
    return talib.SMA(close.astype(np.double), timeperiod)

SMA = vbt.IF(
    input_names=['close', 'high'],
    param_names=['timeperiod'],
    output_names=['sma']
).with_apply_func(
    apply_func_1d,
    takes_1d=True,
    timeperiod=10, #single default
    high=vbt.Ref('close')) #default from another input

ind = SMA.run(s12_data.close)
ind.sma
#sma.sma

symbol                         BAC
time                              
2024-10-03 09:30:00-04:00      NaN
2024-10-03 09:30:12-04:00      NaN
2024-10-03 09:30:24-04:00      NaN
2024-10-03 09:30:36-04:00      NaN
2024-10-03 09:30:48-04:00      NaN
...                            ...
2024-10-16 15:59:00-04:00  42.7735
2024-10-16 15:59:12-04:00  42.7720
2024-10-16 15:59:24-04:00  42.7715
2024-10-16 15:59:36-04:00  42.7730
2024-10-16 15:59:48-04:00  42.7770

[19393 rows x 1 columns]

In [39]:
#vbt.IF.list_indicators("*vwap")
vbt.phelp(vbt.indicator("technical:ROLLING_VWAP").run)


ROLLING_VWAP.run(
    open,
    high,
    low,
    close,
    volume,
    window=Default(value=200),
    min_periods=Default(value=None),
    short_name='rolling_vwap',
    hide_params=None,
    hide_default=True,
    **kwargs
):
    Run `ROLLING_VWAP` indicator.
    
    * Inputs: `open`, `high`, `low`, `close`, `volume`
    * Parameters: `window`, `min_periods`
    * Outputs: `rolling_vwap`
    
    Pass a list of parameter names as `hide_params` to hide their column levels, or True to hide all.
    Set `hide_default` to False to show the column levels of the parameters with a default value.
    
    Other keyword arguments are passed to `ROLLING_VWAP.run_pipeline`.
